# Rule-based approach

## TRAINING DATA
- AnalysisType
- Output
- Context
  - Confidential
  - CellUnits
  - PercentageRows
  - PercentageCellTotal
  - SampleSize
  - PercentageSampleTotal
  - Intercept
  - DegreesOfFreedom
  - DegreesOfFreedom2
  - NumberOfVariables
- Decision

In [1]:
import numpy as np
import pandas as pd
import pickle
from random import shuffle
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.neural_network import MLPClassifier

import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout


import matplotlib.pyplot as plt
%matplotlib inline


# ATTRIBUTES = ['AnalysisType', 
#               'Output', 
#               'Confidential', 
#               'SampleSize', 
#               'NumberOfVariables', 
#               'UnitsPerCell', 
#               'IndUnitContribution',
#               'FreqMode',
#               'MaxIndContribution',
#               'NumberOfParameters',
#               'DegreesOfFreedom',
#               'NumberOfUnitsCorrCoef',
#               'IndependentTerm', # NEW
#               'Decision'
#              ]

ATTRIBUTES = ['AnalysisType',
              'Output',
              'Confidential',
              'CellUnits',
              'PercentageRows',
              'PercentageCellTotal',
              'SampleSize',
              'PercentageSampleTotal',
              'Intercept',
              'DegreesOfFreedom',
              'DegreesOfFreedom2',
              'NumberOfVariables',
              'Decision'
             ]

def init_record(init_value=np.NaN):
    return dict(zip(ATTRIBUTES, [init_value]*len(ATTRIBUTES)))

tf.config.list_physical_devices('GPU')

[]

### Generate training data from rules.

#### RULE 1. 
- AnalysisType
- Output
- Confidential
- CellUnits
- PercentageRows
- Decision
- RULE: 
  - Decision==0, if (Confidential==1 AND (CellUnits < 10 OR PercentageRows >= 90%)).
  - Decision==1, if (Confidential==0 OR (CellUnits >= 10 AND PercentageRows < 90%)).

In [2]:
#DONE
def rule1(decision):
    record = init_record()
    record['AnalysisType'] = 0
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['CellUnits'] = np.random.randint(991) + 10
            record['PercentageRows'] = np.random.random() * 0.9
        else:
            record['CellUnits'] = np.random.randint(1000) + 1
            record['PercentageRows'] = np.random.random()
    else:
        record['Confidential'] = 1
        record['PercentageRows'] = np.random.random()
        if record['PercentageRows'] >= 0.9:
            record['CellUnits'] = np.random.randint(1000) + 1
        else:
            record['CellUnits'] = np.random.randint(9) + 1
            
    record['Decision'] = decision 
    return record

#### RULE 2. 
- AnalysisType
- Output
- Confidential
- CellUnits
- PercentageRows
- PercentageCellTotal
- Decision
- RULE: 
  - Decision==0 if (Confidential==1 AND (CellUnits < 10 OR PercentageRows >= 90% OR PercentageCellTotal >= 50%)).
  - Decision==1 if (Confidential==0 OR (CellUnits >= 10 AND PercentageRows < 90% AND PercentageCellTotal < 50%))

In [3]:
#DONE
def rule2(decision):
    record = init_record()
    record['AnalysisType'] = 1
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['CellUnits'] = np.random.randint(991) + 10
            record['PercentageRows'] = np.random.random() * 0.9
            record['PercentageCellTotal'] = np.random.random() * 0.5
        else:
            record['CellUnits'] = np.random.randint(1000) + 1
            record['PercentageRows'] = np.random.random()
            record['PercentageCellTotal'] = np.random.random()
    else:
        record['Confidential'] = 1
        record['PercentageRows'] = np.random.random()
        if record['PercentageRows'] >= 0.9:
            record['CellUnits'] = np.random.randint(1000) + 1
            record['PercentageCellTotal'] = np.random.random()
        else:
            record['PercentageCellTotal'] = np.random.random()
            if record['PercentageCellTotal'] >= 0.5:
                record['CellUnits'] = np.random.randint(1000) + 1
            else:
                record['CellUnits'] = np.random.randint(9) + 1    
    record['Decision'] = decision
    return record

#### RULES 3a/3b/3c. 
- AnalysisType
- Output
- Confidential
- Decision
- RULE: Decision NO if data confidential

In [4]:
#DONE
def rule3(decision):
    record = init_record()
    record['AnalysisType'] = 2
    record['Output'] = np.random.random()
    record['Confidential'] = 0 if decision else 1
    record['Decision'] = decision
    return record

#### RULE 4. 
- AnalysisType: Mode
- Output: Modal value
- Confidential
- PercentageSampleTotal
- Decision
- Rule: 
  - Decision==0 if (Confidential==1 AND PercentageSampleTotal >= 90%)
  - Decision==1 if (Confidential==0 OR PercentageSampleTotal < 90%)

In [5]:
#DONE
def rule4(decision):
    record = init_record()
    record['AnalysisType'] = 3
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['PercentageSampleTotal'] = np.random.random()
        else:
            record['PercentageSampleTotal'] = np.random.random() * 0.9
    else:
        record['Confidential'] = 1
        record['PercentageSampleTotal'] = np.random.random() * 0.1 + 0.9
                
    record['Decision'] = decision
    return record

#### RULES 5a/5b/5c/5d.
- AnalysisType
- Output
- Confidential
- Sample size
- PercentageSampleTotal.
- Decision
- Rule:
  - Decision==0 NO if (Confidential==1 AND (SampleSize < 10 OR PercentageSampleTotal >= 50%))
  - Decision==1 NO if (Confidential==0 OR (SampleSize >= 10 AND PercentageSampleTotal < 50%)).

In [6]:
#DONE
def rule5(decision):
    record = init_record()
    record['AnalysisType'] = 4
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['SampleSize'] = np.random.randint(990) + 10
            record['PercentageSampleTotal'] = np.random.random() * 0.5
        else:
            record['SampleSize'] = np.random.randint(1000)
            record['PercentageSampleTotal'] = np.random.random()
    else:
        record['Confidential'] = 1
        record['PercentageSampleTotal'] = np.random.random()
        if record['PercentageSampleTotal'] >= 0.5:
            record['SampleSize'] = np.random.randint(1000)
        else:
            record['SampleSize'] = np.random.randint(990) + 10
    record['Decision'] = decision
    return record

#### RULE 6.
- AnalysisType
- Output
- Confidential
- SampleSize
- PercentageSampleTotal
- Decision
- Rule: 
    - Decision NO if (Confidential==1 AND (SampleSize < 10 OR PercentageSampleTotal >= 90%)); 
    - Decision YES if Confidential==0 OR (SampleSize >= 10 AND PercentageSampleTotal < 90%)

In [7]:
#DONE
def rule6(decision):
    record = init_record()
    record['AnalysisType'] = 5
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['SampleSize'] = np.random.randint(990) + 10
            record['PercentageSampleTotal'] = np.random.random() * 0.9
        else:
            record['SampleSize'] = np.random.randint(1000)
            record['PercentageSampleTotal'] = np.random.random()
    else:
        record['Confidential'] = 1
        record['SampleSize'] = np.random.randint(1000)
        if record['SampleSize'] >= 10:
            record['PercentageSampleTotal'] = np.random.random() * 0.1 + 0.9
        else:
            record['PercentageSampleTotal'] = np.random.random()
            
    record['Decision'] = decision
    return record

#### RULES 7a/7b/7c.
- AnalysisType
- Output
- Confidential
- SampleSize.
- Decision
- Rule:
  - Decision==0 if (Confidential==1 AND SampleSize < 10).
  - Decision==1 if (Confidential==0 OR SampleSize >= 10).

In [8]:
#DONE
def rule7(decision):
    record = init_record()
    record['AnalysisType'] = 6
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['SampleSize'] = np.random.randint(990) + 10
        else:
            record['SampleSize'] = np.random.randint(1000)
    else:
        record['Confidential'] = 1
        record['SampleSize'] = np.random.randint(9) + 1

    record['Decision'] = decision
    return record

#### RULE 8.
- AnalysisType: Graph
- Output: Graph
- Context:  Data confidential/not confidential
- Decision: Y/N
- Note: Decision NO if data confidential

In [9]:
#DONE
def rule8(decision):
    record = init_record()
    record['AnalysisType'] = 7
    record['Output'] = np.random.random()
    record['Confidential'] = 0 if decision else 1
    record['Decision'] = decision
    return record

#### RULES 9a/9b.
- AnalysisType: LinearRegressionCoefficients/NonLinearRegressionCoefficients
- Output
- Confidential
- Intercept
- Decision: YES/NO
- Rule:
  - Decision==0 if (Confidential==1 AND Intercept==1).
  - Decision==1 if (Confidential==0 OR Intercept==0).

In [10]:
#DONE
def rule9(decision):
    record = init_record()
    record['AnalysisType'] = 8
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['Intercept'] = 1
        else:
            record['Intercept'] = np.random.randint(2)
    else:
        record['Confidential'] = 1
        record['Intercept'] = 1
        
    record['Decision'] = decision
    return record

#### RULE 10.
- AnalysisType: RegressionResiduals/RegressionResidualsPlot
- Output: Values of residuals/Plot of residuals
- Context: Data confidential/not confidential
- Decision: Y/N
- Note: Decision NO if data confidential

In [11]:
#DONE
def rule10(decision):
    record = init_record()
    record['AnalysisType'] = 9
    record['Output'] = np.random.random()
    record['Confidential'] = 0 if decision else 1
    record['Decision'] = decision
    return record

#### RULES 11a/11b.
- AnalysisType: TestStatistic_t/TestStatistic_F
- Output: Value of statistic
- Context1: Data confidential/not confidential
- Context2: Degrees of freedom
- Decision: Y/N
- Note: Decision NO if (data confidential AND degrees of freedom <10) -> Decision YES if (!data confidential or DoF >= 10)

In [12]:
#TODO: Add second degrees of freedom
def rule11(decision):
    record = init_record()
    record['AnalysisType'] = 10
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential'] == 0:
            record['DegreesOfFreedom'] = np.random.randint(20)+11
        else:
            record['DegreesOfFreedom'] = np.random.randint(30)+1
    else: 
        record['Confidential'] = 1
        record['DegreesOfFreedom'] = np.random.randint(9)+1
    record['Decision'] = decision
    return record

#### RULE 12
- AnalysisType: FactorAnalysis
- Output: Factor scores
- Decision: Y

In [13]:
#DONE
def rule12(decision):
    record = init_record()
    record['AnalysisType'] = 11
    record['Output'] = np.random.random()
    record['Confidential'] = np.random.randint(2)
    record['Decision'] = True
    return record

#### RULE 13.
- AnalysisType: Correlations
- Output: Matrix of correlation coefficients.
- Confidential: YES/NO
- Context: Number of units contributing to each correlation coefficient.
- Decision: YES/NO
- Rule:
  - If data confidential, then the decision is NO for those coefficients that are -1,0,-1 OR that have been computed on less than 10 units.

In [14]:
#DONE
def rule13(decision):
    record = init_record()
    record['AnalysisType'] = 12
    record['Output'] = np.random.random() * 2 - 1
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            while record['Output'] == -1 or record['Output'] == 0 or record['Output'] == 1:
                record['Output'] = np.random.random() * 2 - 1
            record['CellUnits'] = np.random.randint(990) + 10
        else:
            record['CellUnits'] = np.random.randint(1000) + 1
    else:
        record['Confidential'] = 1
        if record['Output'] == -1 or record['Output'] == 0 or record['Output'] == 1:
            record['CellUnits'] = np.random.randint(1000) + 1
        else:
            record['CellUnits'] = np.random.randint(9) + 1
    record['Decision'] = decision
    return record

#### RULE 14.
- AnalysisType: CorrespondenceAnalysis
- Output: Loadings of factors
- Context1: Data confidential/not confidential
- Context2: Number of variables
- Context3: Sample size 
- Decision: Y/N
- Notes: Decision NO if (Confidential==1 AND (number of variables < 2 OR sample size < 10)); Decision YES if Confidential==0 OR (NumberOfVariables >= 2 AND SampleSize >= 10)

In [15]:
#DONE
def rule14(decision):
    record = init_record()
    record['AnalysisType'] = 13
    record['Output'] = np.random.random()
    if decision:
        record['Confidential'] = np.random.randint(2)
        if record['Confidential']:
            record['SampleSize'] = np.random.randint(990) + 10
            record['NumberOfVariables'] = np.random.randint(9) + 2
        else:
            record['SampleSize'] = np.random.randint(1000)
            record['NumberOfVariables'] = np.random.randint(10) + 1
    else:
        record['Confidential'] = 1
        record['SampleSize'] = np.random.randint(1000)
        if record['SampleSize'] >= 10:
            record['NumberOfVariables'] = np.random.randint(2) + 1
        else:
            record['NumberOfVariables'] = np.random.randint(10) + 1
            
    record['Decision'] = decision
    return record

In [16]:
def build_model():
    data_input = Input(shape=(12,))
    x = Dense(64, activation='relu')(data_input)
    x = Dropout(0.1)(x)
    x = Dense(64, activation='relu')(x)
    x = Dropout(0.1)(x)
    output = Dense(1, activation='sigmoid')(x)

    model = Model(data_input, output)
    model.compile(loss='binary_crossentropy',optimizer='adam', metrics=['accuracy'])
    
    return model

def train(data):
    X = np.array(data.drop('Decision', axis=1))
    X = np.nan_to_num(X)
    y = np.array(data['Decision'])
    y = np.nan_to_num(y)

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

    model = build_model()
    
    model.fit(x=X_train, 
              y=y_train, 
              batch_size=64, 
              epochs=20, 
              verbose=1,
              validation_data=(X_test,y_test))
    
    return model

def model_metrics(X, y, model): 
    mat = confusion_matrix(y, np.round(model.predict(X)))
    
    tp = mat[1,1]
    tn = mat[0,0]
    fp = mat[0,1]
    fn = mat[1,0]
    
    result = {}
    result['True Positives'] = tp
    result['True Negatives'] =tn
    result['False Positives'] =fp
    result['False Negatives'] =fn
    result['Accuracy'] = (tp + tn) / (tp + tn + fp + fn)
    result['Positive predictive value (Precision)'] = tp / (tp + fp)
    result['True positive rate (Recall)'] = tp / (tp + fn)
    result['False positive rate (FPR)'] = fp / (fp + tn)
    result['False negative rate (FNR)'] = fn / (fn + tp)
    result['True negative rate (Specificity)'] = tn / (tn + fp)
    result['F1 score'] = 2*tp / (2*tp + fp + fn)
    
    return result

def test(model, data):
    X = np.array(data.drop('Decision', axis=1))
    y = np.array(data['Decision'])
    X = np.nan_to_num(X)
    y = np.nan_to_num(y)
    
    return model_metrics(X, y, model)

def build_training_dataset(training_samples, n_rules, training_samples_per_rule, positive_decision_ratio, training_rules):
    shuffle(training_rules)
    training_dataset = []
    for rule in training_rules[:n_rules]:
        for i in range(int(training_samples_per_rule * positive_decision_ratio)):
            training_dataset.append(rule(True))
        for i in range(int(training_samples_per_rule * (1.0 - positive_decision_ratio))):
            training_dataset.append(rule(False))

    shuffle(training_dataset)
    df = pd.DataFrame(training_dataset)
    return df

def build_testing_dataset(testing_samples_per_rule, positive_decision_ratio, testing_rules):
    testing_dataset = []
    for rule in testing_rules:
        for i in range(int(testing_samples_per_rule * positive_decision_ratio)):
            testing_dataset.append(rule(True))
        for i in range(int(testing_samples_per_rule * (1.0 - positive_decision_ratio))):
            testing_dataset.append(rule(False))

    shuffle(testing_dataset)
    df_test = pd.DataFrame(testing_dataset)
    return df_test

In [17]:
training_samples = 200000
positive_decision_ratio = 0.5
number_of_tests = 100

rules = [rule1,
         rule2,
         rule3,
         rule4,
         rule5,
         rule6,
         rule7,
         rule8,
         rule9,
         rule10,
         rule11,
         rule12,
         rule13,
         rule14]

testing_samples_per_rule = 1000
testing_data = build_testing_dataset(testing_samples_per_rule, positive_decision_ratio, rules)
results = []
for n_rules in range(1,15):
    training_samples_per_rule = int(training_samples / n_rules)
    r = []
    for i in range(number_of_tests):
        print(f'Number of rules: {n_rules}. Test: {i}')
        data = build_training_dataset(training_samples, 
                                      n_rules, 
                                      training_samples_per_rule, 
                                      positive_decision_ratio, 
                                      rules)
        model = train(data)
        r.append(test(model, testing_data))
    results.append(r)

with open('results.pickle', 'wb') as f:
    pickle.dump(results, f)

Number of rules: 1. Test: 0
Epoch 1/20
2094/2094 [==============================] - 1s 704us/step - loss: 1.4211 - accuracy: 0.5186 - val_loss: 0.6782 - val_accuracy: 0.6510
Epoch 2/20
2094/2094 [==============================] - 1s 665us/step - loss: 0.5803 - accuracy: 0.6699 - val_loss: 0.4542 - val_accuracy: 0.7497
Epoch 3/20
2094/2094 [==============================] - 1s 659us/step - loss: 0.4473 - accuracy: 0.7448 - val_loss: 0.3994 - val_accuracy: 0.7487
Epoch 4/20
2094/2094 [==============================] - 1s 668us/step - loss: 0.4021 - accuracy: 0.7495 - val_loss: 0.3936 - val_accuracy: 0.7493
Epoch 5/20
2094/2094 [==============================] - 1s 665us/step - loss: 0.3967 - accuracy: 0.7452 - val_loss: 0.3787 - val_accuracy: 0.7494
Epoch 6/20
2094/2094 [==============================] - 1s 665us/step - loss: 0.3839 - accuracy: 0.7471 - val_loss: 0.3708 - val_accuracy: 0.7495
Epoch 7/20
2094/2094 [==============================] - 1s 662us/step - loss: 0.3929 - accuracy:

Epoch 4/20
2094/2094 [==============================] - 1s 652us/step - loss: 0.1081 - accuracy: 0.9682 - val_loss: 0.1354 - val_accuracy: 0.9524
Epoch 5/20
2094/2094 [==============================] - 1s 649us/step - loss: 0.1084 - accuracy: 0.9672 - val_loss: 0.1200 - val_accuracy: 0.9633
Epoch 6/20
2094/2094 [==============================] - 1s 651us/step - loss: 0.1087 - accuracy: 0.9667 - val_loss: 0.0941 - val_accuracy: 0.9719
Epoch 7/20
2094/2094 [==============================] - 1s 643us/step - loss: 0.1055 - accuracy: 0.9676 - val_loss: 0.1196 - val_accuracy: 0.9725
Epoch 8/20
2094/2094 [==============================] - 1s 642us/step - loss: 0.1094 - accuracy: 0.9657 - val_loss: 0.0957 - val_accuracy: 0.9724
Epoch 9/20
2094/2094 [==============================] - 1s 652us/step - loss: 0.1042 - accuracy: 0.9681 - val_loss: 0.0919 - val_accuracy: 0.9726
Epoch 10/20
2094/2094 [==============================] - 1s 648us/step - loss: 0.1019 - accuracy: 0.9690 - val_loss: 0.0930 

2094/2094 [==============================] - 1s 657us/step - loss: 1.5819e-05 - accuracy: 1.0000 - val_loss: 7.2966e-15 - val_accuracy: 1.0000
Epoch 13/20
2094/2094 [==============================] - 1s 652us/step - loss: 8.9933e-09 - accuracy: 1.0000 - val_loss: 6.4559e-15 - val_accuracy: 1.0000
Epoch 14/20
2094/2094 [==============================] - 1s 651us/step - loss: 6.6389e-08 - accuracy: 1.0000 - val_loss: 5.7959e-16 - val_accuracy: 1.0000
Epoch 15/20
2094/2094 [==============================] - 1s 654us/step - loss: 4.7807e-06 - accuracy: 1.0000 - val_loss: 2.2325e-14 - val_accuracy: 1.0000
Epoch 16/20
2094/2094 [==============================] - 1s 664us/step - loss: 3.3621e-07 - accuracy: 1.0000 - val_loss: 1.7911e-13 - val_accuracy: 1.0000
Epoch 17/20
2094/2094 [==============================] - 1s 660us/step - loss: 1.9879e-08 - accuracy: 1.0000 - val_loss: 2.0814e-14 - val_accuracy: 1.0000
Epoch 18/20
2094/2094 [==============================] - 1s 661us/step - loss: 1.5

Epoch 6/20
2094/2094 [==============================] - 1s 637us/step - loss: 0.1055 - accuracy: 0.9687 - val_loss: 0.1006 - val_accuracy: 0.9687
Epoch 7/20
2094/2094 [==============================] - 1s 641us/step - loss: 0.1027 - accuracy: 0.9692 - val_loss: 0.0983 - val_accuracy: 0.9727
Epoch 8/20
2094/2094 [==============================] - 1s 643us/step - loss: 0.1017 - accuracy: 0.9692 - val_loss: 0.0904 - val_accuracy: 0.9727
Epoch 9/20
2094/2094 [==============================] - 1s 655us/step - loss: 0.1042 - accuracy: 0.9681 - val_loss: 0.0917 - val_accuracy: 0.9727
Epoch 10/20
2094/2094 [==============================] - 1s 634us/step - loss: 0.1034 - accuracy: 0.9683 - val_loss: 0.0904 - val_accuracy: 0.9726
Epoch 11/20
2094/2094 [==============================] - 1s 645us/step - loss: 0.1019 - accuracy: 0.9691 - val_loss: 0.0903 - val_accuracy: 0.9724
Epoch 12/20
2094/2094 [==============================] - 1s 641us/step - loss: 0.1012 - accuracy: 0.9692 - val_loss: 0.124

2094/2094 [==============================] - 1s 643us/step - loss: 0.2224 - accuracy: 0.9252 - val_loss: 0.2217 - val_accuracy: 0.9255
Epoch 15/20
2094/2094 [==============================] - 1s 648us/step - loss: 0.2224 - accuracy: 0.9253 - val_loss: 0.2217 - val_accuracy: 0.9255
Epoch 16/20
2094/2094 [==============================] - 1s 646us/step - loss: 0.2223 - accuracy: 0.9253 - val_loss: 0.2217 - val_accuracy: 0.9255
Epoch 17/20
2094/2094 [==============================] - 1s 655us/step - loss: 0.2224 - accuracy: 0.9252 - val_loss: 0.2217 - val_accuracy: 0.9255
Epoch 18/20
2094/2094 [==============================] - 1s 642us/step - loss: 0.2226 - accuracy: 0.9252 - val_loss: 0.2217 - val_accuracy: 0.9255
Epoch 19/20
2094/2094 [==============================] - 1s 643us/step - loss: 0.2232 - accuracy: 0.9249 - val_loss: 0.2265 - val_accuracy: 0.9255
Epoch 20/20
2094/2094 [==============================] - 1s 652us/step - loss: 0.2236 - accuracy: 0.9247 - val_loss: 0.2218 - val_

...

2094/2094 [==============================] - 1s 691us/step - loss: 0.1666 - accuracy: 0.9246 - val_loss: 0.1391 - val_accuracy: 0.9397
Epoch 19/20
2094/2094 [==============================] - 1s 687us/step - loss: 0.1606 - accuracy: 0.9268 - val_loss: 0.1561 - val_accuracy: 0.9304
Epoch 20/20
2094/2094 [==============================] - 1s 680us/step - loss: 0.1577 - accuracy: 0.9282 - val_loss: 0.1353 - val_accuracy: 0.9410
Number of rules: 14. Test: 74
Epoch 1/20
2094/2094 [==============================] - 1s 712us/step - loss: 0.8390 - accuracy: 0.7895 - val_loss: 0.3496 - val_accuracy: 0.8270
Epoch 2/20
2094/2094 [==============================] - 1s 689us/step - loss: 0.3381 - accuracy: 0.8293 - val_loss: 0.3153 - val_accuracy: 0.8283
Epoch 3/20
2094/2094 [==============================] - 1s 679us/step - loss: 0.3096 - accuracy: 0.8366 - val_loss: 0.2901 - val_accuracy: 0.8424
Epoch 4/20
2094/2094 [==============================] - 1s 690us/step - loss: 0.2772 - accuracy: 0.8593

2094/2094 [==============================] - 1s 681us/step - loss: 0.2928 - accuracy: 0.8448 - val_loss: 0.2798 - val_accuracy: 0.8482
Epoch 5/20
2094/2094 [==============================] - 1s 684us/step - loss: 0.2733 - accuracy: 0.8556 - val_loss: 0.2334 - val_accuracy: 0.8923
Epoch 6/20
2094/2094 [==============================] - 1s 685us/step - loss: 0.2301 - accuracy: 0.8851 - val_loss: 0.1927 - val_accuracy: 0.9118
Epoch 7/20
2094/2094 [==============================] - 1s 677us/step - loss: 0.2014 - accuracy: 0.9068 - val_loss: 0.1698 - val_accuracy: 0.9302
Epoch 8/20
2094/2094 [==============================] - 1s 672us/step - loss: 0.1940 - accuracy: 0.9126 - val_loss: 0.1705 - val_accuracy: 0.9258
Epoch 9/20
2094/2094 [==============================] - 1s 673us/step - loss: 0.1839 - accuracy: 0.9180 - val_loss: 0.1542 - val_accuracy: 0.9346
Epoch 10/20
2094/2094 [==============================] - 1s 688us/step - loss: 0.1816 - accuracy: 0.9199 - val_loss: 0.1644 - val_accur

2094/2094 [==============================] - 1s 685us/step - loss: 0.1610 - accuracy: 0.9282 - val_loss: 0.1440 - val_accuracy: 0.9420
Epoch 15/20
2094/2094 [==============================] - 1s 686us/step - loss: 0.1581 - accuracy: 0.9299 - val_loss: 0.1408 - val_accuracy: 0.9407
Epoch 16/20
2094/2094 [==============================] - 1s 685us/step - loss: 0.1563 - accuracy: 0.9302 - val_loss: 0.1390 - val_accuracy: 0.9420
Epoch 17/20
2094/2094 [==============================] - 1s 687us/step - loss: 0.1608 - accuracy: 0.9282 - val_loss: 0.1342 - val_accuracy: 0.9441
Epoch 18/20
2094/2094 [==============================] - 1s 678us/step - loss: 0.1568 - accuracy: 0.9305 - val_loss: 0.1440 - val_accuracy: 0.9336
Epoch 19/20
2094/2094 [==============================] - 1s 677us/step - loss: 0.1607 - accuracy: 0.9285 - val_loss: 0.1386 - val_accuracy: 0.9348
Epoch 20/20
2094/2094 [==============================] - 1s 680us/step - loss: 0.1506 - accuracy: 0.9323 - val_loss: 0.1311 - val_

2094/2094 [==============================] - 1s 684us/step - loss: 0.2946 - accuracy: 0.8434 - val_loss: 0.2794 - val_accuracy: 0.8472
Epoch 5/20
2094/2094 [==============================] - 1s 680us/step - loss: 0.2840 - accuracy: 0.8471 - val_loss: 0.2689 - val_accuracy: 0.8537
Epoch 6/20
2094/2094 [==============================] - 1s 677us/step - loss: 0.2570 - accuracy: 0.8672 - val_loss: 0.2238 - val_accuracy: 0.8905
Epoch 7/20
2094/2094 [==============================] - 1s 676us/step - loss: 0.2132 - accuracy: 0.8988 - val_loss: 0.1747 - val_accuracy: 0.9139
Epoch 8/20
2094/2094 [==============================] - 1s 669us/step - loss: 0.1924 - accuracy: 0.9122 - val_loss: 0.1672 - val_accuracy: 0.9275
Epoch 9/20
2094/2094 [==============================] - 1s 676us/step - loss: 0.1864 - accuracy: 0.9173 - val_loss: 0.1618 - val_accuracy: 0.9318
Epoch 10/20
2094/2094 [==============================] - 1s 678us/step - loss: 0.1812 - accuracy: 0.9202 - val_loss: 0.1492 - val_accur

2094/2094 [==============================] - 1s 683us/step - loss: 0.1607 - accuracy: 0.9303 - val_loss: 0.1523 - val_accuracy: 0.9378
Epoch 15/20
2094/2094 [==============================] - 1s 685us/step - loss: 0.1588 - accuracy: 0.9304 - val_loss: 0.1461 - val_accuracy: 0.9359
Epoch 16/20
2094/2094 [==============================] - 1s 680us/step - loss: 0.1587 - accuracy: 0.9303 - val_loss: 0.1437 - val_accuracy: 0.9386
Epoch 17/20
2094/2094 [==============================] - 1s 679us/step - loss: 0.1559 - accuracy: 0.9310 - val_loss: 0.1465 - val_accuracy: 0.9335
Epoch 18/20
2094/2094 [==============================] - 1s 678us/step - loss: 0.1506 - accuracy: 0.9334 - val_loss: 0.1461 - val_accuracy: 0.9326
Epoch 19/20
2094/2094 [==============================] - 1s 679us/step - loss: 0.1512 - accuracy: 0.9326 - val_loss: 0.1412 - val_accuracy: 0.9349
Epoch 20/20
2094/2094 [==============================] - 1s 679us/step - loss: 0.1536 - accuracy: 0.9313 - val_loss: 0.1275 - val_

In [18]:
print(results)

[[{'True Positives': 6307, 'True Negatives': 2797, 'False Positives': 3703, 'False Negatives': 1193, 'Accuracy': 0.6502857142857142, 'Positive predictive value (Precision)': 0.6300699300699301, 'True positive rate (Recall)': 0.8409333333333333, 'False positive rate (FPR)': 0.5696923076923077, 'False negative rate (FNR)': 0.15906666666666666, 'True negative rate (Specificity)': 0.4303076923076923, 'F1 score': 0.7203883495145631}, {'True Positives': 6108, 'True Negatives': 4402, 'False Positives': 2098, 'False Negatives': 1392, 'Accuracy': 0.7507142857142857, 'Positive predictive value (Precision)': 0.7443334145747015, 'True positive rate (Recall)': 0.8144, 'False positive rate (FPR)': 0.32276923076923075, 'False negative rate (FNR)': 0.1856, 'True negative rate (Specificity)': 0.6772307692307692, 'F1 score': 0.7777919266522348}, {'True Positives': 1456, 'True Negatives': 6283, 'False Positives': 217, 'False Negatives': 6044, 'Accuracy': 0.5527857142857143, 'Positive predictive value (Pr